In [1]:
import lzma
import numpy as np
from gensim import downloader
from gensim.models import Word2Vec
import gensim.downloader
import pandas as pd
import csv
from sklearn import preprocessing
import vowpalwabbit

In [2]:
train_x = pd.read_csv('train/in.tsv', header=None, sep='\t', quoting=csv.QUOTE_NONE, error_bad_lines=False)
train_y = pd.read_csv('train/expected.tsv', header=None, sep='\t', quoting=csv.QUOTE_NONE, error_bad_lines=False)
dev_x = pd.read_csv('dev-0/in.tsv', header=None, sep='\t', quoting=csv.QUOTE_NONE, error_bad_lines=False)
dev_y = pd.read_csv('dev-0/expected.tsv', header=None, sep='\t', quoting=csv.QUOTE_NONE, error_bad_lines=False)
testa_x = pd.read_csv('test-A/in.tsv', header=None, sep='\t',quoting=csv.QUOTE_NONE, error_bad_lines=False)
testb_x = pd.read_csv('test-B/in.tsv', header=None, sep='\t',quoting=csv.QUOTE_NONE, error_bad_lines=False)

In [3]:
train_x[:10]

0         1                                                  2
0  2004.508197  20040705              Sudan claims it is disarming militias
1  2008.442623  20080611                       Bluffer's guide to Euro 2008
2  2012.587432  20120803          Ennis tallies her highest first day total
3  2009.071233  20090127         Sri Lanka continues to battle Tamil Tigers
4  1997.345205  19970507     Talks today to avert new health service strike
5  2018.046448  20180118  Sunderland end interest in Jon Walters as inju...
6  2010.605479  20100810                Heatwave threatens Russian recovery
7  2001.800000  20011020  Maher's last wish realised as his body is retu...
8  2004.778082  20041011        Two to appear in court over Dunsink protest
9  2017.005479  20170103  Sinn Féin warns Stormont may collapse over 'ca...

In [4]:
dev_x[:10]

0         1                                                  2
0  2014.936986  20141209  President Higgins and Xi Jinping enjoy product...
1  2009.186301  20090310             German trade surplus at seven-year low
2  2019.553425  20190722   Potatoes have 'huge image issue' among the youth
3  2000.554645  20000722  New home education guidelines favour school te...
4  2019.641096  20190823  Mindhunter drags us back to the place where th...
5  2001.158904  20010228  'Asgard' to escape from Kilmainham Gaol and ap...
6  2004.609290  20040811     Five dead after British bus crashes in Austria
7  2012.368852  20120515  Clane General Hospital expects to return to pr...
8  2008.060109  20080123           NI death cert plan 'won't bring closure'
9  2012.791781  20121016  UK investigation into Icelandic bank fraud aba...

In [5]:
testa_x[:10]

0         1                                                 2
0  2011.158904  20110228                  Erratic Wales do it the hard way
1  2018.456284  20180617  Girls in my daughter's class are calling her fat
2  1999.742466  19990929                        Russia 'not ready' for Y2K
3  2000.486339  20000627                                   Those who can't
4  1998.423497  19980605                      Loach returns to Irish theme
5  2005.928767  20051206        Eta says bomb planted in Santander airport
6  2002.467213  20020621                       Inamoto going back to Japan
7  2015.252055  20150403            Neptune Regatta draws big Easter entry
8  2006.005464  20060103                           Brasil One forges ahead
9  2005.569863  20050728     IRA must hand over criminal assets - McDowell

In [6]:
train_y[:10]

0
0   news
1  sport
2   news
3   news
4   news
5  sport
6   news
7   news
8   news
9   news

In [7]:
train_x = train_x[2]
dev_x = dev_x[2]
testa_x = testa_x[2]
testb_x = testb_x[2]

In [8]:
train_x[0]

'Sudan claims it is disarming militias'

In [9]:
train_x

0                   Sudan claims it is disarming militias
1                            Bluffer's guide to Euro 2008
2               Ennis tallies her highest first day total
3              Sri Lanka continues to battle Tamil Tigers
4          Talks today to avert new health service strike
                                ...                      
1186893               Scores of Taliban killed in clashes
1186894                                   Atoms for Peace
1186895          Pope begins biblical pilgrimage in Egypt
1186896               Aer Lingus suspends two more pilots
1186897      Church leaders appeal for restraint and calm
Name: 2, Length: 1186898, dtype: object

In [10]:
train_y[0].unique()

array(['news', 'sport', 'opinion', 'business', 'culture', 'lifestyle',
       'removed'], dtype=object)

In [11]:
le = preprocessing.LabelEncoder()
le.fit(['news', 'sport', 'opinion', 'business', 'culture', 'lifestyle',
       'removed'])
train_y[0] = le.fit_transform(train_y[0])

In [12]:
train_y[:4]

0
0  3
1  6
2  3
3  3

In [13]:
model = vowpalwabbit.Workspace("--oaa 3 --quiet")

In [14]:
train_data = ['{} | headline: {}'.format(y, x) for x,y in zip(train_x,train_y[0])]

In [15]:
type(train_y)

pandas.core.frame.DataFrame

In [16]:
type(train_x)

pandas.core.series.Series

In [17]:
train_data

['3 | headline: Sudan claims it is disarming militias',
 "6 | headline: Bluffer's guide to Euro 2008",
 '3 | headline: Ennis tallies her highest first day total',
 '3 | headline: Sri Lanka continues to battle Tamil Tigers',
 '3 | headline: Talks today to avert new health service strike',
 '6 | headline: Sunderland end interest in Jon Walters as injury strikes again',
 '3 | headline: Heatwave threatens Russian recovery',
 "3 | headline: Maher's last wish realised as his body is returned to Limerick",
 '3 | headline: Two to appear in court over Dunsink protest',
 "3 | headline: Sinn Féin warns Stormont may collapse over 'cash for ash'",
 '3 | headline: Oral hearing into liquid gas pipeline to be held next month',
 '3 | headline: Hopes rise for recovery in chip demand',
 '4 | headline: WELFARE FRAUD',
 "3 | headline: Green Party's key promise up in the air as carbon target appears elusive",
 '6 | headline: It all unravels for Waterford',
 '0 | headline: EU welcomes stability pact but warn

In [18]:
for example in train_data:
    model.learn(example)

In [19]:
def test_set(test_data):
    test = ['| headline: {}'.format(x) for x in test_data]
    return test
    

In [20]:
dev_x = test_set(dev_x)
testa_x = test_set(testa_x)
testb_x = test_set(testb_x)

In [21]:
dev_x[:10]

['| headline: President Higgins and Xi Jinping enjoy productive talks',
 '| headline: German trade surplus at seven-year low',
 "| headline: Potatoes have 'huge image issue' among the youth",
 "| headline: New home education guidelines favour school teachers; says parents' group",
 '| headline: Mindhunter drags us back to the place where the serial killer craze began',
 "| headline: 'Asgard' to escape from Kilmainham Gaol and appear at RDS boat show next week",
 '| headline: Five dead after British bus crashes in Austria',
 '| headline: Clane General Hospital expects to return to profit this year',
 "| headline: NI death cert plan 'won't bring closure'",
 '| headline: UK investigation into Icelandic bank fraud abandoned']

In [22]:
testa_x[:4]

['| headline: Erratic Wales do it the hard way',
 "| headline: Girls in my daughter's class are calling her fat",
 "| headline: Russia 'not ready' for Y2K",
 "| headline: Those who can't"]

In [23]:
def predictions(test_data, out):
    preds = []
    for x in test_data:
        prediction = model.predict(x)
        preds.append(prediction)
    preds = le.inverse_transform(preds)
    file = open(out, 'w')
    for x in preds:
        file.write(f'{x}\n')
    file.close()

In [24]:
predictions(dev_x, 'dev-0\out.tsv')

In [25]:
predictions(testa_x, 'test-A\out.tsv')

In [26]:
predictions(testb_x, 'test-B\out.tsv')